In [4]:
from process_sql import tokenize

In [5]:
from datasets import load_dataset

In [6]:
dataset = load_dataset('spider')

Reusing dataset spider (C:\Users\wasii\.cache\huggingface\datasets\spider\spider\1.0.0\79778ebea87c59b19411f1eb3eda317e9dd5f7788a556d837ef25c3ae6e5e8b7)
100%|██████████| 2/2 [00:00<00:00, 500.04it/s]


In [138]:
dataset[dataset]

DatasetDict({
    train: Dataset({
        features: ['db_id', 'query', 'question', 'query_toks', 'query_toks_no_value', 'question_toks'],
        num_rows: 7000
    })
    validation: Dataset({
        features: ['db_id', 'query', 'question', 'query_toks', 'query_toks_no_value', 'question_toks'],
        num_rows: 1034
    })
})

In [ ]:
from transformers import AutoTokenizer, AutoModel, AutoModelForSeq2SeqLM

model = AutoModelForSeq2SeqLM.from_pretrained("hkunlp/from_all_T5_base_prefix_wikisql2")

In [211]:
model.resize_token_embeddings(len(tokenizer))

Embedding(32102, 768)

In [216]:
from transformers import AutoModelWithLMHead

model2 = AutoModelForSeq2SeqLM.from_pretrained("mrm8488/t5-base-finetuned-wikiSQL")

The `xla_device` argument has been deprecated in v4.4.0 of Transformers. It is ignored and you can safely remove it from your `config.json` file.


In [8]:
tokenizer = AutoTokenizer.from_pretrained("hkunlp/from_all_T5_base_prefix_wikisql2", use_fast=False)

In [256]:
tokenizer = AutoTokenizer.from_pretrained("hkunlp/from_all_T5_base_prefix_spider_with_cell_value2", use_fast=False)

In [41]:
tokenizer2 = AutoTokenizer.from_pretrained("mrm8488/t5-base-finetuned-wikiSQL", use_fast=False)

The `xla_device` argument has been deprecated in v4.4.0 of Transformers. It is ignored and you can safely remove it from your `config.json` file.
The `xla_device` argument has been deprecated in v4.4.0 of Transformers. It is ignored and you can safely remove it from your `config.json` file.


In [34]:
tokenizer2.encode("")

[571, 186, 2250, 130, 1399, 17, 444, 26, 338, 272, 24203, 38, 1247, 825, 58, 1]

In [35]:
tokenizer.decode([571, 186, 2250, 130, 1399, 17, 444, 26, 338, 272, 24203, 38, 1247, 825, 58, 1])

'How many models were finetuned using BERT as base model?</s>'

[3, 2, 7, 3155, 1]

In [257]:
import torch

def get_sql(query):
  input_text = "%s" % query
  features = tokenizer([input_text], max_length=1024, padding="max_length", truncation=True, return_tensors="pt")

  print(features)
  
  output = model.generate(input_ids=features.data['input_ids'],
                #decoder_input_ids = tokenizer2(['<pad>'], return_tensors='pt')['input_ids'],
                attention_mask=features.data['attention_mask'],
                num_beams=1, 
                max_length=256,
                use_cache=True
                )
  
  print(output)
  return tokenizer.batch_decode(output, skip_special_tokens=True)
  #return features

In [233]:
model(input_ids=tokenizer(["get all players"], return_tensors='pt').input_ids, decoder_input_ids=tokenizer(["<pad>"], return_tensors='pt').input_ids)

Seq2SeqLMOutput(loss=None, logits=tensor([[[14.5736,  0.6887, -0.2507,  ...,  0.3256,  1.4639,  1.4921],
         [ 0.7548, 15.2986,  1.5175,  ..., -1.2518,  0.0165,  1.0515]]],
       grad_fn=<UnsafeViewBackward0>), past_key_values=((tensor([[[[ 0.0444, -0.0557,  0.4352,  ..., -0.9208, -0.4168,  0.0811],
          [ 0.8299, -0.2601,  0.4770,  ..., -1.5605,  1.3958, -1.5894]],

         [[ 0.2192,  0.3420,  0.1862,  ...,  0.2967,  0.3893,  0.1522],
          [ 0.5388, -0.4602, -0.0225,  ...,  0.2919,  0.2426,  0.1825]],

         [[ 0.4086, -0.1059,  0.0895,  ...,  0.1341, -0.4958, -0.4717],
          [-0.3785,  0.3537, -0.0888,  ..., -0.0320,  1.2599, -0.3443]],

         ...,

         [[-0.0552, -1.2075, -0.1296,  ...,  0.8638,  0.7624,  0.2997],
          [ 0.1995, -0.5827,  0.5831,  ..., -0.2234, -0.3519,  0.0708]],

         [[-0.0656, -0.0651, -0.8539,  ..., -0.0792, -0.3878,  0.4383],
          [ 1.0318,  1.0345, -0.0536,  ..., -0.2499,  0.9660,  0.4588]],

         [[-0.3505, 

In [254]:
struct_in = "| concert_singer | stadium : stadium_id , location , name , capacity , highest , lowest , average | singer : singer_id , name , country ( France ) , song_name , song_release_year , age , is_male | concert : concert_id , concert_name , theme , stadium_id , year | singer_in_concert : concert_id , singer_id"
text_in = "what is the minimum, average, and maximum age of all singers from France?"

In [259]:
get_sql("{}; structured knowledge: {}".format(text_in, struct_in))

{'input_ids': tensor([[125,  19,   8,  ...,   0,   0,   0]]), 'attention_mask': tensor([[1, 1, 1,  ..., 0, 0, 0]])}
tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])


['']

In [246]:
query = "get all player that are older than 30"
get_sql(query)

{'input_ids': tensor([[ 129,   66, 1959,  ...,    0,    0,    0]]), 'attention_mask': tensor([[1, 1, 1,  ..., 0, 0, 0]])}
tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])


TypeError: int() argument must be a string, a bytes-like object or a number, not 'list'

In [18]:
tokenizer

PreTrainedTokenizer(name_or_path='hkunlp/from_all_T5_base_prefix_wikisql2', vocab_size=32100, model_max_len=512, is_fast=False, padding_side='right', special_tokens={'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<extra_id_40>', '<extra_id_41>', '<extra_id_42>', '<extra_id_43>', '

In [21]:
tokenizer("this is awesome")

{'input_ids': [48, 19, 2879, 1], 'attention_mask': [1, 1, 1, 1]}

In [22]:
tokenizer.decode([48, 19])

'this is'

In [4]:
!pip install sentencepiece

In [17]:
model

T5Model(
  (shared): Embedding(32102, 768)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32102, 768)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=768, out_features=768, bias=False)
              (k): Linear(in_features=768, out_features=768, bias=False)
              (v): Linear(in_features=768, out_features=768, bias=False)
              (o): Linear(in_features=768, out_features=768, bias=False)
              (relative_attention_bias): Embedding(32, 12)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseReluDense(
              (wi): Linear(in_features=768, out_features=3072, bias=False)
              (wo): Linear(in_features=3072, out_features=768, bias=False)
              (dropout): Dropout(p=0.1, inplac

In [3]:
dataset

DatasetDict({
    train: Dataset({
        features: ['db_id', 'query', 'question', 'query_toks', 'query_toks_no_value', 'question_toks'],
        num_rows: 7000
    })
    validation: Dataset({
        features: ['db_id', 'query', 'question', 'query_toks', 'query_toks_no_value', 'question_toks'],
        num_rows: 1034
    })
})

In [9]:
dataset['train']['db_id']

['department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessm

In [8]:
dataset['train']['query_toks']

[['SELECT', 'count', '(', '*', ')', 'FROM', 'head', 'WHERE', 'age', '>', '56'],
 ['SELECT',
  'name',
  ',',
  'born_state',
  ',',
  'age',
  'FROM',
  'head',
  'ORDER',
  'BY',
  'age'],
 ['SELECT',
  'creation',
  ',',
  'name',
  ',',
  'budget_in_billions',
  'FROM',
  'department'],
 ['SELECT',
  'max',
  '(',
  'budget_in_billions',
  ')',
  ',',
  'min',
  '(',
  'budget_in_billions',
  ')',
  'FROM',
  'department'],
 ['SELECT',
  'avg',
  '(',
  'num_employees',
  ')',
  'FROM',
  'department',
  'WHERE',
  'ranking',
  'BETWEEN',
  '10',
  'AND',
  '15'],
 ['SELECT',
  'name',
  'FROM',
  'head',
  'WHERE',
  'born_state',
  '!',
  '=',
  "'California",
  "'"],
 ['SELECT',
  'DISTINCT',
  'T1.creation',
  'FROM',
  'department',
  'AS',
  'T1',
  'JOIN',
  'management',
  'AS',
  'T2',
  'ON',
  'T1.department_id',
  '=',
  'T2.department_id',
  'JOIN',
  'head',
  'AS',
  'T3',
  'ON',
  'T2.head_id',
  '=',
  'T3.head_id',
  'WHERE',
  'T3.born_state',
  '=',
  "'Alabama"

In [20]:
set(dataset['validation']['db_id'])

{'battle_death',
 'car_1',
 'concert_singer',
 'course_teach',
 'cre_Doc_Template_Mgt',
 'dog_kennels',
 'employee_hire_evaluation',
 'flight_2',
 'museum_visit',
 'network_1',
 'orchestra',
 'pets_1',
 'poker_player',
 'real_estate_properties',
 'singer',
 'student_transcripts_tracking',
 'tvshow',
 'voter_1',
 'world_1',
 'wta_1'}

In [22]:
from process_sql import get_sql, get_schema, Schema
import os

error_indices = []
num_errors = 0

for ex_num in range(len(dataset['validation'])):
    example = dataset['validation'][ex_num]
    schema = Schema(get_schema(os.path.join('database', example['db_id'], example['db_id'] + '.sqlite')))
    sql = get_sql(schema, example['query'])

In [6]:
dataset['train']['db_id']

['department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'department_management',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'farm',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessment',
 'student_assessm

In [4]:
import importlib
import process_sql

importlib.reload(process_sql)

<module 'process_sql' from 'c:\\Users\\wasii\\Documents\\NLP_Class_Project\\process_sql.py'>

In [ ]:
#pip install -r requirements.txt

In [ ]:
import nltk
nltk.download('punkt')

In [ ]:
tokenize(r'SELECT * FROM AIRPORTS WHERE city  =  "Anthony"')

In [2]:
import pickle

dataset = None

with open("dataset/classical_test_bug_free.pkl", "rb") as file:
    dataset = pickle.load(file)

In [3]:
import datasets

In [26]:
import random

random.seed(10)

random.shuffle(dataset)

train_data = dataset[:int(len(dataset) * .8)]
test_data = dataset[int(len(dataset) * .8):]

In [3]:
inputs = [ex['text'] for ex in dataset]
targets = [ex['query'] for ex in dataset]
target_db_paths = [ex['db_path'] for ex in dataset]

In [32]:
train_data

[{'text': "i'm looking for flights from SAN FRANCISCO to ATLANTA leaving before 800",
  'query': 'SELECT DISTINCT FLIGHTalias0.FLIGHT_ID FROM AIRPORT_SERVICE AS AIRPORT_SERVICEalias0 , AIRPORT_SERVICE AS AIRPORT_SERVICEalias1 , CITY AS CITYalias0 , CITY AS CITYalias1 , FLIGHT AS FLIGHTalias0 WHERE ( CITYalias1.CITY_CODE = AIRPORT_SERVICEalias1.CITY_CODE AND CITYalias1.CITY_NAME = "ATLANTA" AND FLIGHTalias0.DEPARTURE_TIME < 800 AND FLIGHTalias0.TO_AIRPORT = AIRPORT_SERVICEalias1.AIRPORT_CODE ) AND CITYalias0.CITY_CODE = AIRPORT_SERVICEalias0.CITY_CODE AND CITYalias0.CITY_NAME = "SAN FRANCISCO" AND FLIGHTalias0.FROM_AIRPORT = AIRPORT_SERVICEalias0.AIRPORT_CODE ;',
  'variables': [{'example': 'ATLANTA',
    'location': 'unk',
    'name': 'city_name0',
    'type': 'city_name',
    'ancestor_of_occuring_column': {('city', 'CITY_NAME')}},
   {'example': '800',
    'location': 'unk',
    'name': 'departure_time0',
    'type': 'departure_time',
    'ancestor_of_occuring_column': {('flight', 'A

In [37]:
datasets.IterableDataset([{'text': 'hmm', 'query': 'wow'}])

AttributeError: 'IterableDataset' object has no attribute 'column_names'

In [50]:
import pandas as pd 

dataset_pd = pd.DataFrame(dataset)

In [51]:
dataset_pd = dataset_pd[['text', 'query', 'variables', 'db_path']]

In [56]:
raw_dataset = datasets.Dataset.from_pandas(dataset_pd)

In [58]:
dataset_dict = datasets.DatasetDict({
    "train": raw_dataset, 
})

In [59]:
dataset_dict['train'].train_test_split(test_size=int(len(raw_dataset) * .2))

DatasetDict({
    train: Dataset({
        features: ['text', 'query', 'variables', 'db_path'],
        num_rows: 2808
    })
    test: Dataset({
        features: ['text', 'query', 'variables', 'db_path'],
        num_rows: 701
    })
})

In [60]:
dataset_dict['train'].column_names

['text', 'query', 'variables', 'db_path']

In [39]:
dataset_dict.column_names

AttributeError: 'IterableDatasetDict' object has no attribute 'column_names'

In [33]:
dataset_dict["train"].column_names

TypeError: Values in `DatasetDict` should of type `Dataset` but got type '<class 'list'>'

In [ ]:
import sklearn
from sklearn.feature_extraction.text import CountVectorizer

In [ ]:
import transformers
from transformers import PreTrainedTokenizerFast
from tokenizers import Tokenizer
from tokenizers.models import BPE
from tokenizers.trainers import BpeTrainer
from tokenizers.pre_tokenizers import Whitespace
from tokenizers import Tokenizer

In [ ]:
source_tokenizer = Tokenizer(BPE(unk_token="[UNK]"))
source_tokenizer_trainer = BpeTrainer(special_tokens=["[UNK]", "[PAD]", "[BOS]", "[EOS]"])
source_tokenizer.pre_tokenizer = Whitespace()

source_iterator = (item for item in train_data)
source_tokenizer.train_from_iterator(
    source_iterator,
    trainer=source_tokenizer_trainer,
)

source_tokenizer = transformers.PreTrainedTokenizerFast(
    tokenizer_object=source_tokenizer,
    bos_token="[BOS]",
    eos_token="[EOS]",
    pad_token="[PAD]",
)

In [ ]:
source_tokenizer(inputs, max_length=100, truncation=True)

In [ ]:
target_vectorizer = CountVectorizer(lowercase=True, tokenizer=tokenize)

In [ ]:
target_vectorizer = target_vectorizer.fit(targets)

In [ ]:
targets_vectorized = target_vectorizer.transform(targets)

In [ ]:
target_vectorizer.transform(['return me the papers on PVLDB']).toarray()

In [ ]:
target_vectorizer.vocabulary_

In [ ]:
len(target_vectorizer.vocabulary_)

In [ ]:
word_id_tups = list(target_vectorizer.vocabulary_.items())

word_id_tups

In [ ]:
import numpy as np

(target_vectorizer.transform(targets) > 0).nonzero()

In [6]:
def build_ids_vector(targets):
    arr = []
    for row in target_vectorizer.transform(targets).toarray():
        arr.append([0] + (row > 0).nonzero()[0])

    return arr

In [7]:
build_ids_vector(targets)

NameError: name 'target_vectorizer' is not defined

In [ ]:
targets[200]

In [ ]:
target_db_paths[20]

In [ ]:
targets[300].strip()

In [ ]:
targets[0].strip()

In [ ]:
targets[23].strip().replace('(', '').replace(')', ''))

In [ ]:
tokenize(targets[20].replace(',', ' '))

In [10]:
for key in schema.schema:
    print(key)

aircraft
airline
airport
airport_service
city
class_of_service
code_description
compartment_class
date_day
days
dual_carrier
equipment_sequence
fare
fare_basis
flight
flight_fare
flight_leg
flight_stop
food_service
ground_service
month
restriction
state
time_interval
time_zone


In [7]:
targets[0].strip()

'SELECT DISTINCT FLIGHTalias0.FLIGHT_ID FROM AIRPORT_SERVICE AS AIRPORT_SERVICEalias0 , AIRPORT_SERVICE AS AIRPORT_SERVICEalias1 , CITY AS CITYalias0 , CITY AS CITYalias1 , FLIGHT AS FLIGHTalias0 WHERE ( CITYalias1.CITY_CODE = AIRPORT_SERVICEalias1.CITY_CODE AND CITYalias1.CITY_NAME = "ATLANTA" AND FLIGHTalias0.DEPARTURE_TIME < 800 AND FLIGHTalias0.TO_AIRPORT = AIRPORT_SERVICEalias1.AIRPORT_CODE ) AND CITYalias0.CITY_CODE = AIRPORT_SERVICEalias0.CITY_CODE AND CITYalias0.CITY_NAME = "SAN FRANCISCO" AND FLIGHTalias0.FROM_AIRPORT = AIRPORT_SERVICEalias0.AIRPORT_CODE ;'

In [9]:
tokenize(targets[0])

['select',
 'distinct',
 'flightalias0.flight_id',
 'from',
 'airport_service',
 'as',
 'airport_servicealias0',
 ',',
 'airport_service',
 'as',
 'airport_servicealias1',
 ',',
 'city',
 'as',
 'cityalias0',
 ',',
 'city',
 'as',
 'cityalias1',
 ',',
 'flight',
 'as',
 'flightalias0',
 'where',
 '(',
 'cityalias1.city_code',
 '=',
 'airport_servicealias1.city_code',
 'and',
 'cityalias1.city_name',
 '=',
 '"ATLANTA"',
 'and',
 'flightalias0.departure_time',
 '<',
 '800',
 'and',
 'flightalias0.to_airport',
 '=',
 'airport_servicealias1.airport_code',
 ')',
 'and',
 'cityalias0.city_code',
 '=',
 'airport_servicealias0.city_code',
 'and',
 'cityalias0.city_name',
 '=',
 '"SAN FRANCISCO"',
 'and',
 'flightalias0.from_airport',
 '=',
 'airport_servicealias0.airport_code',
 ';']

In [ ]:
#error col 9 (

In [33]:
len(targets)
#567

2807

In [9]:
sql_vocab = [
    'select', 'from', 'where', 'group', 'order', 'limit', 'intersect', 'union', 'except', 'by', 'having', 'distinct',
    'join', 'on', 'as', 'outer', 'inner',
    'not', 'between', '=', '>', '<', '>=', '<=', '!=', 'in', 'like', 'is', 'exists',
    'none', 'max', 'min', 'count', 'sum', 'avg',
    'and', 'or',
    'intersect', 'union', 'except',
    'desc', 'asc',
    ',', '(', ')', ';', '*'
]

In [3]:
BOS_INDEX = 0
UNK_INDEX = 1
EOS_INDEX = len(sql_vocab) + 2
PAD_INDEX = len(sql_vocab) + 3

NameError: name 'sql_vocab' is not defined

In [11]:
def build_sql_id_vector(str):
    tokens = tokenize(str.lower())

    ids = []
    for token in tokens:
        if token in sql_vocab:
            ids.append(sql_vocab.index(token) + 2)
        else:
            ids.append(UNK_INDEX)
    return ids

In [12]:
sql_ids = []

for ex in targets:
    sql_ids.append(build_sql_id_vector(ex))

In [13]:
targets[30]

'SELECT DISTINCT COUNT( CITEalias0.CITINGPAPERID ) , WRITESalias1.AUTHORID FROM AUTHOR AS AUTHORalias0 , CITE AS CITEalias0 , WRITES AS WRITESalias0 , WRITES AS WRITESalias1 WHERE AUTHORalias0.AUTHORNAME = "Luke Zettlemoyer" AND WRITESalias0.AUTHORID = AUTHORalias0.AUTHORID AND WRITESalias0.PAPERID = CITEalias0.CITEDPAPERID AND WRITESalias1.PAPERID = CITEalias0.CITINGPAPERID GROUP BY WRITESalias1.AUTHORID ORDER BY COUNT( CITEalias0.CITINGPAPERID ) DESC ;'

In [11]:
tokenize(targets[30])

['select',
 'distinct',
 'count',
 '(',
 'citealias0.citingpaperid',
 ')',
 ',',
 'writesalias1.authorid',
 'from',
 'author',
 'as',
 'authoralias0',
 ',',
 'cite',
 'as',
 'citealias0',
 ',',
 'writes',
 'as',
 'writesalias0',
 ',',
 'writes',
 'as',
 'writesalias1',
 'where',
 'authoralias0.authorname',
 '=',
 '"Luke Zettlemoyer"',
 'and',
 'writesalias0.authorid',
 '=',
 'authoralias0.authorid',
 'and',
 'writesalias0.paperid',
 '=',
 'citealias0.citedpaperid',
 'and',
 'writesalias1.paperid',
 '=',
 'citealias0.citingpaperid',
 'group',
 'by',
 'writesalias1.authorid',
 'order',
 'by',
 'count',
 '(',
 'citealias0.citingpaperid',
 ')',
 'desc',
 ';']

In [14]:
sql_ids[30]

[2,
 13,
 34,
 45,
 1,
 46,
 44,
 1,
 3,
 1,
 16,
 1,
 44,
 1,
 16,
 1,
 44,
 1,
 16,
 1,
 44,
 1,
 16,
 1,
 4,
 1,
 21,
 1,
 37,
 1,
 21,
 1,
 37,
 1,
 21,
 1,
 37,
 1,
 21,
 1,
 5,
 11,
 1,
 6,
 11,
 34,
 45,
 1,
 46,
 42,
 47]

In [17]:
import utils

padded_sql_ids = utils.pad(sql_ids, PAD_INDEX)

In [18]:
padded_sql_ids

tensor([[ 2, 13,  1,  ..., 50, 50, 50],
        [ 2, 13,  1,  ..., 50, 50, 50],
        [ 2, 34, 45,  ..., 50, 50, 50],
        ...,
        [ 2, 13,  1,  ..., 50, 50, 50],
        [ 2, 34, 45,  ..., 50, 50, 50],
        [ 2, 13,  1,  ..., 50, 50, 50]])

In [23]:
build_sql_id_vector('SELECT * FROM AIRPORTS WHERE city  =  "Anthony"')

[2, 47, 3, 1, 4, 1, 20, 1]

In [24]:
dataset

[{'text': "i'm looking for flights from SAN FRANCISCO to ATLANTA leaving before 800",
  'query': 'SELECT DISTINCT FLIGHTalias0.FLIGHT_ID FROM AIRPORT_SERVICE AS AIRPORT_SERVICEalias0 , AIRPORT_SERVICE AS AIRPORT_SERVICEalias1 , CITY AS CITYalias0 , CITY AS CITYalias1 , FLIGHT AS FLIGHTalias0 WHERE ( CITYalias1.CITY_CODE = AIRPORT_SERVICEalias1.CITY_CODE AND CITYalias1.CITY_NAME = "ATLANTA" AND FLIGHTalias0.DEPARTURE_TIME < 800 AND FLIGHTalias0.TO_AIRPORT = AIRPORT_SERVICEalias1.AIRPORT_CODE ) AND CITYalias0.CITY_CODE = AIRPORT_SERVICEalias0.CITY_CODE AND CITYalias0.CITY_NAME = "SAN FRANCISCO" AND FLIGHTalias0.FROM_AIRPORT = AIRPORT_SERVICEalias0.AIRPORT_CODE ;',
  'variables': [{'example': 'ATLANTA',
    'location': 'unk',
    'name': 'city_name0',
    'type': 'city_name',
    'ancestor_of_occuring_column': {('city', 'CITY_NAME')}},
   {'example': '800',
    'location': 'unk',
    'name': 'departure_time0',
    'type': 'departure_time',
    'ancestor_of_occuring_column': {('flight', 'A

In [10]:
targets[10]

'SELECT COUNT( DISTINCT ( PUBLICATIONalias0.TITLE ) ) FROM AUTHOR AS AUTHORalias0 , CONFERENCE AS CONFERENCEalias0 , PUBLICATION AS PUBLICATIONalias0 , WRITES AS WRITESalias0 WHERE AUTHORalias0.NAME = "H. V. Jagadish" AND CONFERENCEalias0.NAME = "VLDB" AND PUBLICATIONalias0.CID = CONFERENCEalias0.CID AND WRITESalias0.AID = AUTHORalias0.AID AND WRITESalias0.PID = PUBLICATIONalias0.PID ;'

In [73]:
tokenize(targets[10])

['select',
 'count',
 '(',
 'distinct',
 '(',
 'publicationalias0.title',
 ')',
 ')',
 'from',
 'author',
 'as',
 'authoralias0',
 ',',
 'conference',
 'as',
 'conferencealias0',
 ',',
 'publication',
 'as',
 'publicationalias0',
 ',',
 'writes',
 'as',
 'writesalias0',
 'where',
 'authoralias0.name',
 '=',
 '"H. V. Jagadish"',
 'and',
 'conferencealias0.name',
 '=',
 '"VLDB"',
 'and',
 'publicationalias0.cid',
 '=',
 'conferencealias0.cid',
 'and',
 'writesalias0.aid',
 '=',
 'authoralias0.aid',
 'and',
 'writesalias0.pid',
 '=',
 'publicationalias0.pid',
 ';']

In [14]:
targets[9]

'SELECT DISTINCT COURSEalias0.DEPARTMENT , COURSEalias0.NAME , COURSEalias0.NUMBER FROM COURSE AS COURSEalias0 WHERE COURSEalias0.CREDITS = 3 AND COURSEalias0.DEPARTMENT = "EECS" AND COURSEalias0.NUMBER < 400 + 100 AND COURSEalias0.NUMBER >= 400 ;'

In [17]:
targets[10]

'SELECT COUNT( DISTINCT ( PUBLICATIONalias0.TITLE ) ) FROM AUTHOR AS AUTHORalias0 , CONFERENCE AS CONFERENCEalias0 , PUBLICATION AS PUBLICATIONalias0 , WRITES AS WRITESalias0 WHERE AUTHORalias0.NAME = "H. V. Jagadish" AND CONFERENCEalias0.NAME = "VLDB" AND PUBLICATIONalias0.CID = CONFERENCEalias0.CID AND WRITESalias0.AID = AUTHORalias0.AID AND WRITESalias0.PID = PUBLICATIONalias0.PID ;'

In [10]:
len(targets)

2807

In [ ]:
new_targets

In [9]:
len(targets)

3509

In [5]:
from process_sql import get_sql, get_schema, Schema
import os

error_indices = []
num_errors = 0

for num in range(len(targets)):
    try:
        schema = Schema(get_schema(target_db_paths[num]))
        sql = get_sql(schema, targets[num])
    except:
        num_errors += 1
        error_indices.append(num)
        print(str(num) + ":", targets[num])

print(num_errors)



16: SELECT AUTHORalias0.NAME FROM AUTHOR AS AUTHORalias0 , JOURNAL AS JOURNALalias0 , PUBLICATION AS PUBLICATIONalias0 , WRITES AS WRITESalias0 WHERE JOURNALalias0.NAME = "PVLDB" AND PUBLICATIONalias0.JID = JOURNALalias0.JID AND PUBLICATIONalias0.YEAR = 2010 AND WRITESalias0.AID = AUTHORalias0.AID AND WRITESalias0.PID = PUBLICATIONalias0.PID ;
17: SELECT AUTHORalias0.NAME FROM AUTHOR AS AUTHORalias0 , JOURNAL AS JOURNALalias0 , PUBLICATION AS PUBLICATIONalias0 , WRITES AS WRITESalias0 WHERE JOURNALalias0.NAME = "PVLDB" AND PUBLICATIONalias0.JID = JOURNALalias0.JID AND PUBLICATIONalias0.YEAR > 2010 AND WRITESalias0.AID = AUTHORalias0.AID AND WRITESalias0.PID = PUBLICATIONalias0.PID ;
18: SELECT AUTHORalias0.NAME FROM AUTHOR AS AUTHORalias0 , CONFERENCE AS CONFERENCEalias0 , PUBLICATION AS PUBLICATIONalias0 , WRITES AS WRITESalias0 WHERE CONFERENCEalias0.NAME = "VLDB" AND PUBLICATIONalias0.CID = CONFERENCEalias0.CID AND PUBLICATIONalias0.YEAR = 2002 AND WRITESalias0.AID = AUTHORalias0.AI

In [13]:
new_targets = [i for j, i in enumerate(targets) if j not in error_indices]
new_target_db_paths = [i for j, i in enumerate(target_db_paths) if j not in error_indices]

In [10]:
new_dataset = [i for j, i in enumerate(dataset) if j not in error_indices]

In [11]:
with open('dataset/classical_test_bug_free.pkl', 'wb') as handle:
    pickle.dump(new_dataset, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [4]:
num_errors = 0

for num in range(len(new_targets)):
    try:
        schema = Schema(get_schema(new_target_db_paths[num]))
        sql = get_sql(schema, new_targets[num])
    except:
        num_errors += 1
        error_indices.append(num)
        print(str(num) + ":", new_targets[num])

print(num_errors)


NameError: name 'new_targets' is not defined

In [ ]:
glist[405]

In [ ]:

with open('dataset/classical_test_gold.txt') as f:
    gseq_one = []
    glist = []

    for l in f.readlines():
        glist.append(l.strip())
    
    print(glist[0])

In [ ]:
glist[405]

In [ ]:
schema.idMap